In [1]:
#Selenium

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time
import csv

# Function to read usernames and passwords from CSV
def read_credentials_from_csv(file_path):
    credentials = []
    with open(file_path, "r") as csvfile:
        reader = csv.DictReader(csvfile)
        for row in reader:
            credentials.append((row["username"], row["password"]))
    return credentials

# Start a Web Browser Session
driver = webdriver.Chrome("C:/Users/Warit/Webdrivers/chromedriver.exe")

# Open the login page of the website
driver.get("https://www.dataforthai.com/login")

# Read usernames and passwords from CSV
credentials_file = "credentials.csv"
users_credentials = read_credentials_from_csv(credentials_file)

for username, password in users_credentials:

    driver = webdriver.Chrome("C:/Users/Warit/Webdrivers/chromedriver.exe")
    driver.get("https://www.dataforthai.com/login")

    # Find the username and password input fields and enter the credentials
    username_input = driver.find_element(By.NAME, 'username')  # Replace "username" with the actual name attribute of the username input field
    password_input = driver.find_element('name', 'password')  # Replace "password" with the actual name attribute of the password input field

    username_input.send_keys(username)
    password_input.send_keys(password)

    # Submit the login form
    login_button = driver.find_element(By.XPATH, '//*[@id="btn-login"]')  # Replace the XPath with the correct XPath of the login button
    login_button.click()

    # After login, get the value of the "PHPSESSID" cookie
    phpsessid_cookie = driver.get_cookie("PHPSESSID")
    if phpsessid_cookie:
        phpsessid_value = phpsessid_cookie["value"]
        print(f"Value of 'PHPSESSID' cookie: {phpsessid_value}")
    else:
        print("PHPSESSID cookie not found.")

    # time.sleep(3)

    # cookie_denied_btn = driver.find_element(By.XPATH, '//*/a[@id="dft-decline-btn"]').click()

    # time.sleep(1)

    # logout_btn = driver.find_element(By.XPATH, '//*/a[@id="LogoutBtn"]').click()

    time.sleep(3)

    # After login, you can perform any actions on the logged-in page as needed
    # For example, you can access different pages, interact with elements, or scrape data.

#driver.quit()


C:\Users\Warit\AppData\Local\Temp\ipykernel_66652\316613523.py:19: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("C:/Users/Warit/Webdrivers/chromedriver.exe")
C:\Users\Warit\AppData\Local\Temp\ipykernel_66652\316613523.py:30: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("C:/Users/Warit/Webdrivers/chromedriver.exe")


Value of 'PHPSESSID' cookie: 11vr6p8ac29jbqkvdgqb05jaug
Value of 'PHPSESSID' cookie: o019jpqeb6lhok79tc8cu2uehj
Value of 'PHPSESSID' cookie: 6ap5o5iksluoaondq96rgbhv5a
Value of 'PHPSESSID' cookie: cactjtvtifbt4ofuqub7hm7k4s


: 

In [ ]:
#Selenium + Scrap Code
import csv
import requests
import json
import numpy as np
import pandas as pd
import time
import random
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from parsel import Selector
from datetime import datetime

# Function to read usernames and passwords from CSV
def read_credentials_from_csv(file_path):
    credentials = []
    with open(file_path, "r") as csvfile:
        reader = csv.DictReader(csvfile)
        for row in reader:
            credentials.append((row["username"], row["password"]))
    return credentials

while True:

    df = pd.read_csv('./dataforthai_test2.csv', dtype={'tax': str, 'tsic': str})

    # File path to store and load the value of 'i'
    index_file = './last_index.txt'

    # Load the last index value if the file exists
    try:
        with open(index_file, 'r') as file:
            last_index = int(file.read().strip())
    except FileNotFoundError:
        last_index = None

    # Set the parameter value as the sum of 'i' and 25
    break_parameter = last_index + 15 if last_index is not None else None

    # PAYLOAD & COOKIES FOR LOGGING TO DATAFORTHAI
    payload = {}
    cookies = {"PHPSESSID": "9q3qnjo10523de97toup1r8cuj"}
     

    # Create a session object for HTTP requests
    session = requests.Session()

    # PROCESS SCRAPING
    for i, v in enumerate(df.iterrows()):
        if last_index is not None and i <= last_index:
            continue
        
        if v[1]['name_en'] == '-':
            tax = v[1]['tax']
            tsic_code = v[1]['tsic']
            url = f'https://dataforthai.com/company/{tax}/'
            
            # Use the session object for the request
            req = session.get(url, cookies=cookies, params=json.dumps(payload))

            selector = Selector(text=req.text)
            created_at = datetime.now().isoformat()
            df.at[i, 'name_en'] = selector.xpath('//*/div[@id="main"]//h2/text()').get().strip()
            container_body = selector.xpath('//*/div[@id="main"]/div[3]/table[1]/tr/td')[0]
            df.at[i, 'business'] = container_body.xpath('//*/table[2]/tr[1]/td[2]/text()[1]').get().strip()
            df.at[i, 'status'] = container_body.xpath('//*/table[3]/tr/td[2]/text()').get().strip()
            df.at[i, 'date_register_thai'] = container_body.xpath('//*/table[4]/tr/td[2]/text()').get().strip()
            df.at[i, 'capital'] = container_body.xpath('//*/table[5]/tr/td[2]/text()').get().strip()
            address_element = container_body.xpath('//*/table[6]/tr/td[2]/a/text()')
            df.at[i, 'address'] = address_element.get().strip() if address_element else ""
            
            # Use list comprehension for committee lists
            list_committee = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[8]/tr/td/text()').getall()]
            list_committee_other = [committee.strip() for committee in container_body.xpath('//*/tr/td/table[9]/tr/td/text()').getall()]
            df.at[i, 'list_committee'] = list_committee + list_committee_other

            df.to_csv('./dataforthai_test2.csv', encoding='utf-8', index=False)
            
            # Save the current index value to the file
            with open(index_file, 'w') as file:
                file.write(str(i))
            
            sleep_time = random.uniform(10, 20)
            time.sleep(sleep_time)

    time.sleep(65)

In [ ]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By


chrome_options = webdriver.ChromeOptions()
prefs = {
                "profile.default_content_setting_values.notifications" : 2,
                "translate_whitelists": {"es":"en"},
                "translate":{"enabled":"true"}
                }
chrome_options.add_argument("user-agent=Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) HeadlessChrome/96.0.4664.110 Safari/537.36")
chrome_options.add_experimental_option("prefs",prefs)
# chrome_options.headless = False
chrome_options.add_argument('--no-sandbox')
# chrome_options.add_argument('--headless')
chrome_options.add_argument('--disable-gpu')
chrome_options.add_argument('--disable-dev-shm-usage')
chrome_options.add_argument("--window-size=1920,1080")
driver = webdriver.Chrome(options=chrome_options)